In [53]:
import pandas as pd
import openpyxl
import numpy as np
from collections import Counter
import random
from datetime import timedelta
from mlxtend.frequent_patterns import apriori, association_rules
np.random.seed(42)

In [2]:
df_orig = pd.read_excel('Online Retail.xlsx')
df = df_orig.copy() # removing cancelled orders from this dataframe for easier analysis

In [3]:
df_cancelled = df_orig[df_orig['InvoiceNo'].str.contains(r'c', case=False, na=False)]
df_cancelled

InvoiceNo StockCode                       Description  Quantity  \
141      C536379         D                          Discount        -1   
154      C536383    35004C   SET OF 3 COLOURED  FLYING DUCKS        -1   
235      C536391     22556    PLASTERS IN TIN CIRCUS PARADE        -12   
236      C536391     21984  PACK OF 12 PINK PAISLEY TISSUES        -24   
237      C536391     21983  PACK OF 12 BLUE PAISLEY TISSUES        -24   
...          ...       ...                               ...       ...   
540449   C581490     23144   ZINC T-LIGHT HOLDER STARS SMALL       -11   
541541   C581499         M                            Manual        -1   
541715   C581568     21258        VICTORIAN SEWING BOX LARGE        -5   
541716   C581569     84978  HANGING HEART JAR T-LIGHT HOLDER        -1   
541717   C581569     20979     36 PENCILS TUBE RED RETROSPOT        -5   

               InvoiceDate  UnitPrice  CustomerID         Country  
141    2010-12-01 09:41:00      27.50     14527.0  United Kingdom  
154    2010-12-01 09:49:00       4.65     15311.0  United Kingdom  
235    2010-12-01 10:24:00       1.65     17548.0  United Kingdom  
236    2010-12-01 10:24:00       0.29     17548.0  United Kingdom  
237    2010-12-01 10:24:00       0.29     17548.0  United Kingdom  
...                    ...        ...         ...             ...  
540449 2011-12-09 09:57:00       0.83     14397.0  United Kingdom  
541541 2011-12-09 10:28:00     224.69     15498.0  United Kingdom  
541715 2011-12-09 11:57:00      10.95     15311.0  United Kingdom  
541716 2011-12-09 11:58:00       1.25     17315.0  United Kingdom  
541717 2011-12-09 11:58:00       1.25     17315.0  United Kingdom  

[9288 rows x 8 columns]

In [4]:
                    
df = df.drop(df_cancelled.index)   # dropping cancelled orders as they do not have any impact on the following analyses

In [5]:
print(df.shape)

print(df.isna().any())

print(df['CustomerID'].isna().sum())

print(df.dtypes)

(532621, 8)
InvoiceNo      False
StockCode      False
Description     True
Quantity       False
InvoiceDate    False
UnitPrice      False
CustomerID      True
Country        False
dtype: bool
134697
InvoiceNo              object
StockCode              object
Description            object
Quantity                int64
InvoiceDate    datetime64[ns]
UnitPrice             float64
CustomerID            float64
Country                object
dtype: object


In [6]:
#Two columns have NaN values: 'Description' and 'CustomerID'. Both need to be imputed.
df[df['Description'].isna()]['StockCode']

622        22139
1970       21134
1971       22145
1972       37509
1987      85226A
           ...  
535322     84581
535326     23406
535332     21620
536981     72817
538554     85175
Name: StockCode, Length: 1454, dtype: object

'Description' imputation:
It is suspected that missing descriptions can be imputed by values from the sam StockCode since they each code is supposed to point to a product. For this purpose, stockcodes of the missing descriptions have been taken and 10 of them will be tested out to see if this is truly the case.

In [7]:
df[df['StockCode']==21777]['Description']

19       RECIPE BOX WITH METAL HEART
2140     RECIPE BOX WITH METAL HEART
2399     RECIPE BOX WITH METAL HEART
2406                             NaN
2587     RECIPE BOX WITH METAL HEART
10350    RECIPE BOX WITH METAL HEART
11104    RECIPE BOX WITH METAL HEART
12008                            NaN
Name: Description, dtype: object

Out of the 10 tested, around 3 showed rows in which the same values present over and over, just like the value above, strengthening the hypothesis. But observations also showed that minor changes in values or no values altogther is to be expected. 
IMPUTATION STRATEGY: For now, using mode grouping description by stockcode to impute the missing Description col values. If stockcodes with no sample descriptions for imputations are seen, using np.nan for them and later, if they are still present, using mode to impute the rows.

In [8]:
df['Description'] = df.groupby('StockCode')['Description'].transform(lambda x:x.fillna(x.mode()[0]) if not x.mode().empty else np.nan)
df['Description'].isna().sum()    # NaN numbers have reduced, but 112 still remain NaN
df['Description'] = df['Description'].fillna(df['Description'].mode()[0]) # NaN numbers = 0; Commiting this change

Description has been imputed, but CustomerID still has NaNs, and can be hypothesized to have ties to Country col. Imputing based on it.
IMPUTATION STRATEGY: grouping customerID based on Country, and imputing based on mode.

In [9]:
df['CustomerID'] = df.groupby('Country')['CustomerID'].transform(lambda x:x.fillna(x.mode()[0]) if not x.mode().empty else np.nan)
df[df['CustomerID'].isna()]['Country'].value_counts()

Country
Hong Kong    284
Name: count, dtype: int64

CustomerID has been imputed based on Country values. Imputing the remaining NaN values (Hong Kong did not have sample Customer IDs for the imputation) with a few fake customer IDs.

In [10]:
print(df['CustomerID'].min())       #finding max and min of customer ID to produce 5 realistic fake customers
print(df['CustomerID'].max())

12346.0
18287.0


In [11]:
unique_customers = set(df['CustomerID'].dropna().unique())
required_fakes = 10
fake_customers = []

while len(fake_customers) < required_fakes:
    number = random.randint(12346, 18287)
    if number not in unique_customers:
        fake_customers.append(number)
        unique_customers.add(number)

fake_customers                    # acquired 10 fake customer IDs, using these to impute the rest of CustomerID NaNs.
    


[17130, 14402, 16845, 16329, 13757, 13480, 17137, 14812, 17963, 17156]

In [ ]:
df['CustomerID'] = df['CustomerID'].fillna(random.choice(fake_customers))
df[df['CustomerID'].isna()]['Country'].value_counts()   #nothing in the output confirms that there are no NaN values in CustomerID

Series([], Name: count, dtype: int64)

FEATURE ENGINEERING: Creating columns:
- 'Order price' by multiplying quantity and unit price to get total price of each order and, 
- 'Category', by calculating the number of words in each product, ranking them according to their frequency, and assignilng the highest ranked words as category to that product.

In [13]:
df['order_price'] = (df['UnitPrice'] * df['Quantity']).round(2)


To Feature Engineer 'Category', we are splitting the words in the description, ranking them according to their overall frequency, and assigning the words that occur the most and is present in a word as its category. We are also excluding some words which have very high frequency, but cannot pass as 'categories' (such as articles) from becoming categories. We do this by running the counter, checking for the highest freqeuncy words, and adding unsuitable words from them into an exclusion list and running the counter with it. We iterate this again and again till we get about twenty of the top frequency words as proper terms that can pass as 'categories'.

In [14]:
df['Description'] = df['Description'].astype(str).str.lower()
word_bucket = df['Description'].str.extractall(r'(\w+)')[0]
word_bucket

        match
0       0            white
        1          hanging
        2            heart
        3                t
        4            light
                   ...    
541908  0           baking
        1              set
        2                9
        3            piece
        4        retrospot
Name: 0, Length: 2373093, dtype: object

In [ ]:
ex_words = ex_words = ['of','3','and','in','on','12','6','w', 'with']   #words to be excluded when creating 'categories'
ranked_words = [word for word in word_bucket.groupby(word_bucket).count().sort_values(ascending=False).index if word not in ex_words]

In [16]:
# category_generator function which checks the words in a description, checks which of them has occurred the most in the dataset, and assigns
# that word as the category

def category_generator(phrase):
    for word in ranked_words:
        if word in phrase.split():
            return word
    return 'Misc'
            

In [17]:
df['Category'] = df['Description'].apply(category_generator)


RECENCY SCORE:
Identifying the most recent purchase made by each of the customers and calculating the days between that and a fixed analysis date (one day after the last recorded transaction in this case). Storing this date against each of the unique customer IDs to assign a Recency Score for each of them as part of the RMF profile analysis.

In [18]:
analysis_date = df['InvoiceDate'].max() + timedelta(days=1)
analysis_date


Timestamp('2011-12-10 12:50:00')

In [19]:
recency = df.groupby('CustomerID')['InvoiceDate'].max().reset_index()
recency['day_diff'] = (analysis_date - recency['InvoiceDate']).dt.days
recency['r_score'] = pd.qcut(recency['day_diff'], q=5, labels=[5,4,3,2,1]) #more recent (less days) the better
recency  = recency.rename({'InvoiceDate':'last_order_date'}, axis=1)
recency

CustomerID     last_order_date  day_diff r_score
0        12346.0 2011-01-18 10:01:00       326       1
1        12347.0 2011-12-07 15:52:00         2       5
2        12348.0 2011-09-25 13:13:00        75       2
3        12349.0 2011-11-21 09:51:00        19       4
4        12350.0 2011-02-02 16:01:00       310       1
...          ...                 ...       ...     ...
4335     18280.0 2011-03-07 09:52:00       278       1
4336     18281.0 2011-06-12 10:53:00       181       1
4337     18282.0 2011-12-02 11:43:00         8       5
4338     18283.0 2011-12-06 12:02:00         4       5
4339     18287.0 2011-10-28 09:29:00        43       3

[4340 rows x 4 columns]

In [20]:
frequency = df.groupby('CustomerID')['InvoiceNo'].count().reset_index()
frequency['f_score'] = pd.qcut(frequency['InvoiceNo'], q=5, labels = [1,2,3,4,5]) #more is better
frequency = frequency.rename({'InvoiceNo':'Order_Count'}, axis=1)
frequency

CustomerID  Order_Count f_score
0        12346.0            1       1
1        12347.0          182       5
2        12348.0           31       3
3        12349.0           73       4
4        12350.0           17       2
...          ...          ...     ...
4335     18280.0           10       1
4336     18281.0            7       1
4337     18282.0           12       1
4338     18283.0          756       5
4339     18287.0           70       4

[4340 rows x 3 columns]

In [21]:
monetary = df.groupby('CustomerID')['order_price'].sum().reset_index()
monetary['m_score'] = pd.qcut(monetary['order_price'], q=5, labels = [1,2,3,4,5]) #higher is better
monetary = monetary.rename({'order_price':'total_spend'}, axis=1)
monetary

CustomerID  total_spend m_score
0        12346.0     77183.60       5
1        12347.0      4310.00       5
2        12348.0      1797.24       4
3        12349.0      1757.55       4
4        12350.0       334.40       2
...          ...          ...     ...
4335     18280.0       180.60       1
4336     18281.0        80.82       1
4337     18282.0       178.05       1
4338     18283.0      2094.88       5
4339     18287.0      1837.28       4

[4340 rows x 3 columns]

In [22]:
# recency, frequency and monetary scores have been calculated in separate tables. Putting them together 
# and aggregating their score to form an RFM profile for each customer

customer_behavior = pd.DataFrame()
customer_behavior = recency.merge(frequency, on='CustomerID').merge(monetary, on='CustomerID')
customer_behavior = customer_behavior[['CustomerID', 'last_order_date', 'day_diff', 'Order_Count',
        'total_spend','f_score','r_score', 'm_score']]


In [45]:
                                ##creating RFM segments based on the R, F and M scores calculated##
customer_behavior['customer_profile'] = (
                          customer_behavior['r_score'].astype(str) +
                          customer_behavior['f_score'].astype(str) +
                          customer_behavior['m_score'].astype(str)
                          )
customer_behavior

CustomerID     last_order_date  day_diff  Order_Count  total_spend  \
0        12346.0 2011-01-18 10:01:00       326            1     77183.60   
1        12347.0 2011-12-07 15:52:00         2          182      4310.00   
2        12348.0 2011-09-25 13:13:00        75           31      1797.24   
3        12349.0 2011-11-21 09:51:00        19           73      1757.55   
4        12350.0 2011-02-02 16:01:00       310           17       334.40   
...          ...                 ...       ...          ...          ...   
4335     18280.0 2011-03-07 09:52:00       278           10       180.60   
4336     18281.0 2011-06-12 10:53:00       181            7        80.82   
4337     18282.0 2011-12-02 11:43:00         8           12       178.05   
4338     18283.0 2011-12-06 12:02:00         4          756      2094.88   
4339     18287.0 2011-10-28 09:29:00        43           70      1837.28   

     f_score r_score m_score customer_profile  
0          1       1       5              115  
1          5       5       5              555  
2          3       2       4              234  
3          4       4       4              444  
4          2       1       2              122  
...      ...     ...     ...              ...  
4335       1       1       1              111  
4336       1       1       1              111  
4337       1       5       1              511  
4338       5       5       5              555  
4339       4       3       4              344  

[4340 rows x 9 columns]

In [51]:
                                ##creating an overall summary table with single value KPIs##
repeat_rate = round(((df.groupby('CustomerID')['InvoiceNo'].nunique()>1).sum()/(df['CustomerID'].nunique())*100), 2)
sold_quantity = df['Quantity'].sum()
customer_count = df['CustomerID'].nunique()
gross_revenue = int(df['order_price'].sum())
total_orders = int(df['InvoiceNo'].count())
overall_avg_basket_size = int((df['Quantity'].sum()/df['Quantity'].count()))
# cancellation metrics
cancel_rate = round(df_cancelled['InvoiceNo'].nunique()/(df['InvoiceNo'].nunique()), 2)
cancel_quantity = abs(df_cancelled['Quantity'].sum())

overall_kpis = pd.DataFrame({
    "total_orders": [total_orders],
    "sold_quantity": [sold_quantity],
    "gross_revenue": [gross_revenue],
    "customer_count": [customer_count],
    "overall_avg_basket_size": [overall_avg_basket_size],
    "repeat_rate": [repeat_rate],
    "cancel_rate": [cancel_rate],
    "cancel_quantity": [cancel_quantity]
})

overall_kpis

total_orders  sold_quantity  gross_revenue  customer_count  \
0        532621        5454024       10644560            4340   

   overall_avg_basket_size  repeat_rate  cancel_rate  cancel_quantity  
0                       10        65.62         0.17           277574

PRODUCT EFFECIENCY ANALYSIS:
- Because of the limitations of the available data, we will not be delving into KPIs which involve the product's cost price, and will be focusing on the basket size and cancellation rate per product.

In [25]:
#Basket size analysis
basket_size = pd.DataFrame()
basket_size_customer = df.groupby('CustomerID')['Quantity'].sum()
basket_size_country = df.groupby('Country')['Quantity'].count()
basket_size_season = df.groupby(df['InvoiceDate'].dt.to_period('M'))['Quantity'].count()
basket_size_daily = df.groupby(df['InvoiceDate'].dt.to_period('D'))['Quantity'].count()
basket_size_perorder_avg = (df.groupby('InvoiceNo')['Quantity'].sum()/df.groupby('InvoiceNo')['Quantity'].count()).round(2)



In [26]:
bought_together = df.groupby('InvoiceNo')['StockCode'].unique().reset_index()
ohe = bought_together.explode('StockCode')
ohe.columns


Index(['InvoiceNo', 'StockCode'], dtype='object')

In [27]:
apriori_feed = (pd.crosstab(ohe['InvoiceNo'], ohe['StockCode'])).astype(bool)
apriori_feed

StockCode  10002  10080  10120  10125  10133  10134  10135  11001  15030  \
InvoiceNo                                                                  
536365     False  False  False  False  False  False  False  False  False   
536366     False  False  False  False  False  False  False  False  False   
536367     False  False  False  False  False  False  False  False  False   
536368     False  False  False  False  False  False  False  False  False   
536369     False  False  False  False  False  False  False  False  False   
...          ...    ...    ...    ...    ...    ...    ...    ...    ...   
581586     False  False  False  False  False  False  False  False  False   
581587     False  False  False  False  False  False  False  False  False   
A563185    False  False  False  False  False  False  False  False  False   
A563186    False  False  False  False  False  False  False  False  False   
A563187    False  False  False  False  False  False  False  False  False   

StockCode  15034  ...      M   PADS   POST      S  gift_0001_10  gift_0001_20  \
InvoiceNo         ...                                                           
536365     False  ...  False  False  False  False         False         False   
536366     False  ...  False  False  False  False         False         False   
536367     False  ...  False  False  False  False         False         False   
536368     False  ...  False  False  False  False         False         False   
536369     False  ...  False  False  False  False         False         False   
...          ...  ...    ...    ...    ...    ...           ...           ...   
581586     False  ...  False  False  False  False         False         False   
581587     False  ...  False  False  False  False         False         False   
A563185    False  ...  False  False  False  False         False         False   
A563186    False  ...  False  False  False  False         False         False   
A563187    False  ...  False  False  False  False         False         False   

StockCode  gift_0001_30  gift_0001_40  gift_0001_50      m  
InvoiceNo                                                   
536365            False         False         False  False  
536366            False         False         False  False  
536367            False         False         False  False  
536368            False         False         False  False  
536369            False         False         False  False  
...                 ...           ...           ...    ...  
581586            False         False         False  False  
581587            False         False         False  False  
A563185           False         False         False  False  
A563186           False         False         False  False  
A563187           False         False         False  False  

[22064 rows x 4059 columns]

In [28]:
frequent_sets = apriori(apriori_feed, min_support=0.02,use_colnames=True)

In [29]:
support_rules = association_rules(frequent_sets, metric="support", min_threshold=0.03) 
confidence_rules = association_rules(frequent_sets, metric="confidence", min_threshold=0.3)
lift_rules = association_rules(frequent_sets, metric="lift", min_threshold=1.2)
lift_rules.head()


antecedents consequents  antecedent support  consequent support   support  \
0     (20712)     (21931)            0.039113            0.053662  0.020350   
1     (21931)     (20712)            0.053662            0.039113  0.020350   
2     (20712)    (85099B)            0.039113            0.094815  0.024248   
3    (85099B)     (20712)            0.094815            0.039113  0.024248   
4     (20724)     (20719)            0.046864            0.037844  0.022933   

   confidence       lift  representativity  leverage  conviction  \
0    0.520278   9.695453               1.0  0.018251    1.972680   
1    0.379223   9.695453               1.0  0.018251    1.547877   
2    0.619930   6.538311               1.0  0.020539    2.381630   
3    0.255736   6.538311               1.0  0.020539    1.291056   
4    0.489362  12.930870               1.0  0.021160    1.884221   

   zhangs_metric   jaccard  certainty  kulczynski  
0       0.933366  0.280976   0.493075    0.449751  
1       0.947715  0.280976   0.353954    0.449751  
2       0.881535  0.221074   0.580119    0.437833  
3       0.935781  0.221074   0.225440    0.437833  
4       0.968031  0.371240   0.469277    0.547675

In [30]:
#creating StockCode to product description map to use it later in the antecedent and consequent stock code mapping 
stock_desc_map = (df.groupby('StockCode')['Description'].apply(lambda x:x.mode()[0]))

In [31]:
def rules_cleaner(df):      # to extract values from frozen sets association rules antecedents and consequents
    df['antecedents'] = df['antecedents'].apply(lambda x:list(x)[0])
    df['consequents'] = df['consequents'].apply(lambda x:list(x)[0])
    df['antec_desc'] = df['antecedents'].map(stock_desc_map)
    df['conseq_desc'] = df['consequents'].map(stock_desc_map)
    df = df.drop(columns=['representativity', 'leverage', 'conviction', 'zhangs_metric',
       'jaccard', 'certainty', 'kulczynski'])
    df =     df[['antecedents', 'consequents', 'antec_desc', 'conseq_desc', 'antecedent support',
       'consequent support', 'support', 'confidence', 'lift']]
    return df

In [32]:
cleaned_confidence = rules_cleaner(confidence_rules.copy())
cleaned_lift = rules_cleaner(lift_rules.copy())
cleaned_support = rules_cleaner(support_rules.copy())

In [48]:
                                ##cleaning and storing support, confidence and lift values for visualization##
cleaned_confidence = (cleaned_confidence.sort_values(by=['confidence'], ascending=False)).head(20)
cleaned_lift = (cleaned_lift.sort_values(by=['lift'], ascending=False)).head(20)
cleaned_support = (cleaned_support.sort_values(by=['support'], ascending=False)).head(20)


In [34]:
cleaned_lift

antecedents consequents                          antec_desc  \
123       22697       22698     green regency teacup and saucer   
126       22698       22697      pink regency teacup and saucer   
125       22697       22698     green regency teacup and saucer   
124       22698       22697      pink regency teacup and saucer   
91        22698       22697      pink regency teacup and saucer   
90        22697       22698     green regency teacup and saucer   
127       22699       22697    roses regency teacup and saucer    
122       22697       22699     green regency teacup and saucer   
112       23300       23301  gardeners kneeling pad cup of tea    
113       23301       23300   gardeners kneeling pad keep calm    
95        22699       22698    roses regency teacup and saucer    
94        22698       22699      pink regency teacup and saucer   
92        22697       22699     green regency teacup and saucer   
93        22699       22697    roses regency teacup and saucer    
89        22630       22629                dolly girl lunch box   
88        22629       22630                 spaceboy lunch box    
13        22356       20724         charlotte bag pink polkadot   
12        20724       22356         red retrospot charlotte bag   
9         20724       20723         red retrospot charlotte bag   
8         20723       20724            strawberry charlotte bag   

                            conseq_desc  antecedent support  \
123      pink regency teacup and saucer            0.034808   
126     green regency teacup and saucer            0.034763   
125      pink regency teacup and saucer            0.046003   
124     green regency teacup and saucer            0.027148   
91      green regency teacup and saucer            0.034763   
90       pink regency teacup and saucer            0.046003   
127     green regency teacup and saucer            0.048314   
122    roses regency teacup and saucer             0.028689   
112   gardeners kneeling pad keep calm             0.034355   
113  gardeners kneeling pad cup of tea             0.041380   
95       pink regency teacup and saucer            0.048314   
94     roses regency teacup and saucer             0.034763   
92     roses regency teacup and saucer             0.046003   
93      green regency teacup and saucer            0.048314   
89                  spaceboy lunch box             0.038524   
88                 dolly girl lunch box            0.040790   
13          red retrospot charlotte bag            0.033675   
12          charlotte bag pink polkadot            0.046864   
9              strawberry charlotte bag            0.046864   
8           red retrospot charlotte bag            0.032723   

     consequent support   support  confidence       lift  
123            0.034763  0.024565    0.705729  20.301445  
126            0.034808  0.024565    0.706649  20.301445  
125            0.027148  0.024565    0.533990  19.669380  
124            0.046003  0.024565    0.904841  19.669380  
91             0.046003  0.028689    0.825293  17.940170  
90             0.034763  0.028689    0.623645  17.940170  
127            0.028689  0.024565    0.508443  17.722404  
122            0.048314  0.024565    0.856240  17.722404  
112            0.041380  0.024746    0.720317  17.407520  
113            0.034355  0.024746    0.598028  17.407520  
95             0.034763  0.027148    0.561914  16.164360  
94             0.048314  0.027148    0.780965  16.164360  
92             0.048314  0.034808    0.756650  15.661099  
93             0.046003  0.034808    0.720450  15.661099  
89             0.040790  0.024384    0.632941  15.516905  
88             0.038524  0.024384    0.597778  15.516905  
13             0.046864  0.023658    0.702557  14.991511  
12             0.033675  0.023658    0.504836  14.991511  
9              0.032723  0.022027    0.470019  14.363583  
8              0.046864  0.022027    0.673130  14.363583

In [52]:
df

InvoiceNo StockCode                          Description  Quantity  \
0         536365    85123A   white hanging heart t-light holder         6   
1         536365     71053                  white metal lantern         6   
2         536365    84406B       cream cupid hearts coat hanger         8   
3         536365    84029G  knitted union flag hot water bottle         6   
4         536365    84029E       red woolly hottie white heart.         6   
...          ...       ...                                  ...       ...   
541904    581587     22613          pack of 20 spaceboy napkins        12   
541905    581587     22899         children's apron dolly girl          6   
541906    581587     23254        childrens cutlery dolly girl          4   
541907    581587     23255      childrens cutlery circus parade         4   
541908    581587     22138        baking set 9 piece retrospot          3   

               InvoiceDate  UnitPrice  CustomerID         Country  \
0      2010-12-01 08:26:00       2.55     17850.0  United Kingdom   
1      2010-12-01 08:26:00       3.39     17850.0  United Kingdom   
2      2010-12-01 08:26:00       2.75     17850.0  United Kingdom   
3      2010-12-01 08:26:00       3.39     17850.0  United Kingdom   
4      2010-12-01 08:26:00       3.39     17850.0  United Kingdom   
...                    ...        ...         ...             ...   
541904 2011-12-09 12:50:00       0.85     12680.0          France   
541905 2011-12-09 12:50:00       2.10     12680.0          France   
541906 2011-12-09 12:50:00       4.15     12680.0          France   
541907 2011-12-09 12:50:00       4.15     12680.0          France   
541908 2011-12-09 12:50:00       4.95     12680.0          France   

        order_price   Category  
0             15.30      heart  
1             20.34      metal  
2             22.00      cream  
3             20.34     bottle  
4             20.34        red  
...             ...        ...  
541904        10.20       pack  
541905        12.60      dolly  
541906        16.60      dolly  
541907        16.60  childrens  
541908        14.85        set  

[532621 rows x 10 columns]

In [54]:
df.to_excel("cleaned_df.xlsx", index=False)
cleaned_lift.to_excel("cleaned_lift.xlsx", index=False)
cleaned_support.to_excel("cleaned_support.xlsx", index=False)
overall_kpis.to_excel("overall_kpis.xlsx", index=False)

